In [2]:
# Space Debris Simulation - Fixed for Google Colab
!pip install -q plotly

import numpy as np
import plotly.graph_objects as go

# ---------- Config ----------
N_debris = 1000
frames = 80
duration_seconds = 3600 * 4
R_earth = 6371.0
mu = 398600.4418
np.random.seed(42)
# ----------------------------

# Region probabilities
region_probs = {"LEO": 0.85, "MEO": 0.10, "GEO": 0.05}
regions = np.random.choice(list(region_probs.keys()), size=N_debris, p=list(region_probs.values()))

# Altitudes
alts = np.zeros(N_debris)
for i, r in enumerate(regions):
    if r == "LEO":
        alts[i] = np.random.choice([300, 800, 1000, 1200], p=[0.2, 0.4, 0.3, 0.1]) + np.random.randn()*30
    elif r == "MEO":
        alts[i] = np.random.uniform(2000, 20000)
    else:
        alts[i] = 35786 + np.random.randn()*50

a = R_earth + alts
theta0 = np.random.uniform(0, 2*np.pi, N_debris)
raan = np.random.uniform(0, 2*np.pi, N_debris)
inc = np.deg2rad(np.random.uniform(0, 180, N_debris))
argp = np.random.uniform(0, 2*np.pi, N_debris)
n = np.sqrt(mu / (a**3))
t_vec = np.linspace(0, duration_seconds, frames)

positions = np.zeros((frames, N_debris, 3), dtype=np.float32)

for i, t in enumerate(t_vec):
    theta = theta0 + n * t
    x_op = a * np.cos(theta)
    y_op = a * np.sin(theta)

    ca = np.cos(argp); sa = np.sin(argp)
    x1 = ca * x_op - sa * y_op
    y1 = sa * x_op + ca * y_op
    z1 = np.zeros_like(x1)

    ci = np.cos(inc); si = np.sin(inc)
    x2 = x1
    y2 = ci * y1 - si * z1
    z2 = si * y1 + ci * z1

    cr = np.cos(raan); sr = np.sin(raan)
    x = cr * x2 - sr * y2
    y = sr * x2 + cr * y2
    z = z2

    positions[i] = np.stack((x, y, z), axis=1)

colors = ["orange" if r == "LEO" else "yellow" if r == "MEO" else "red" for r in regions]

# Earth sphere
u = np.linspace(0, 2*np.pi, 40)
v = np.linspace(0, np.pi, 20)
x_s = R_earth * np.outer(np.cos(u), np.sin(v))
y_s = R_earth * np.outer(np.sin(u), np.sin(v))
z_s = R_earth * np.outer(np.ones_like(u), np.cos(v))
earth_surf = go.Surface(x=x_s, y=y_s, z=z_s, colorscale='Blues', showscale=False, opacity=0.9)

# First frame
scatter0 = go.Scatter3d(
    x=positions[0,:,0], y=positions[0,:,1], z=positions[0,:,2],
    mode='markers',
    marker=dict(size=2, color=colors, opacity=0.8),
    hoverinfo='skip'
)

frames_data = []
for fi in range(frames):
    frames_data.append(go.Frame(
        data=[
            earth_surf,
            go.Scatter3d(
                x=positions[fi,:,0],
                y=positions[fi,:,1],
                z=positions[fi,:,2],
                mode='markers',
                marker=dict(size=2, color=colors, opacity=0.8),
                hoverinfo='skip'
            )
        ],
        name=str(fi)
    ))

fig = go.Figure(
    data=[earth_surf, scatter0],
    layout=go.Layout(
        title="Space Debris Simulation (LEO / MEO / GEO)",
        scene=dict(
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
            aspectmode='data'
        ),
        updatemenus=[dict(type="buttons", showactive=False, buttons=[
            dict(label="Play", method="animate", args=[None, {"frame": {"duration": 60, "redraw": True}}]),
            dict(label="Pause", method="animate", args=[[None], {"frame": {"duration": 0, "redraw": False}}])
        ])]
    ),
    frames=frames_data
)

fig.show()
